## Importing Dependencies

In [ ]:
import tensorflow as tf
import math
import random
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import pandas_datareader as data_reader
import yfinance as yf

from tqdm import tqdm_notebook, tqdm
from collections import deque

# Check if TensorFlow is using the GPU
print(tf.config.list_physical_devices("GPU"))


[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


In [ ]:
print("CUDA support:", tf.test.is_built_with_cuda())


CUDA support: True


In [ ]:
tf.__version__

'2.12.0'

## Building the AI Trader network

In [ ]:
class AI_Trader():
  
  def __init__(self, state_size, action_space=3, model_name="AITrader"): #Stay, Buy, Sell
    
    self.state_size = state_size
    self.action_space = action_space
    self.memory = deque(maxlen=2000)
    self.inventory = []
    self.model_name = model_name
    
    self.gamma = 0.95
    self.epsilon = 1.0
    self.epsilon_final = 0.01
    self.epsilon_decay = 0.995
    
    self.model = self.model_builder()
    
  def model_builder(self):
    
    model = tf.keras.models.Sequential()
    
    model.add(tf.keras.layers.Dense(units=32, activation='relu', input_dim=self.state_size))
    
    model.add(tf.keras.layers.Dense(units=64, activation='relu'))
    
    model.add(tf.keras.layers.Dense(units=128, activation='relu'))
    
    model.add(tf.keras.layers.Dense(units=self.action_space, activation='linear'))
    
    model.compile(loss='mse', optimizer=tf.keras.optimizers.Adam(lr=0.001))
    
    return model
  
  def trade(self, state):
    
    if random.random() <= self.epsilon:
      return random.randrange(self.action_space)
    
    actions = self.model.predict(state)
    return np.argmax(actions[0])
  
  
  def batch_train(self, batch_size):
    
    batch = []
    for i in range(len(self.memory) - batch_size + 1, len(self.memory)):
      batch.append(self.memory[i])
      
    for state, action, reward, next_state, done in batch:
      reward = reward
      if not done:
        reward = reward + self.gamma * np.amax(self.model.predict(next_state)[0])
        
      target = self.model.predict(state)
      target[0][action] = reward
      
      self.model.fit(state, target, epochs=1, verbose=0)
      
    if self.epsilon > self.epsilon_final:
      self.epsilon *= self.epsilon_decay

### Dataset Preprocessing

#### Sigmoid

In [ ]:
def sigmoid(x):
  return 1 / (1 + math.exp(-x))

#### Price format function

In [ ]:
def stocks_price_format(n):
  if n < 0:
    return "- $ {0:2f}".format(abs(n))
  else:
    return "$ {0:2f}".format(abs(n))

#### Dataset Loader

In [ ]:
def dataset_loader(stock_name):
  
  dataset = yf.download(stock_name)
  
  start_date = str(dataset.index[0]).split()[0]
  end_date = str(dataset.index[-1]).split()[0]
  
  close = dataset['Close']

  return close

#### State Creator

In [ ]:
def state_creator(data, timestep, window_size):
  
  starting_id = timestep - window_size + 1
  
  if starting_id >= 0:
    windowed_data = data[starting_id:timestep+1]
  else:
    windowed_data = - starting_id * [data[0]] + list(data[0:timestep+1])
    
  state = []
  for i in range(window_size - 1):
    state.append(sigmoid(windowed_data[i+1] - windowed_data[i]))
    
  return np.array([state])

#### Loading a Dataset

In [ ]:
stock_name = "AAPL"
data = dataset_loader(stock_name)

[*********************100%***********************]  1 of 1 completed


In [ ]:
data

Date
1980-12-12      0.128348
1980-12-15      0.121652
1980-12-16      0.112723
1980-12-17      0.115513
1980-12-18      0.118862
                 ...    
2023-05-22    174.199997
2023-05-23    171.559998
2023-05-24    171.839996
2023-05-25    172.990005
2023-05-26    175.429993
Name: Close, Length: 10704, dtype: float64

#### Setting hyper parameters

In [ ]:
window_size = 10


### Defining the Trader model

In [ ]:
trader = AI_Trader(window_size)

In [ ]:
trader.model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 32)                352       
                                                                 
 dense_1 (Dense)             (None, 64)                2112      
                                                                 
 dense_2 (Dense)             (None, 128)               8320      
                                                                 
 dense_3 (Dense)             (None, 3)                 387       
                                                                 
Total params: 11,171
Trainable params: 11,171
Non-trainable params: 0
_________________________________________________________________


### Training Agent

In [ ]:
episodes = 10
data_samples = len(data)- window_size # Replace with the actual number of data samples

# Initialize variables
best_profit = float("-inf")

# Run the episodes
for episode in range(1, episodes + 1):
    print("Episode: {}/{}".format(episode, episodes))

    state = state_creator(data, 0, window_size + 1)
    total_profit = 0
    trader.inventory = []

    # Loop over the data samples
    for t in tqdm(range(data_samples)):
        action = trader.trade(state)

        next_state = state_creator(data, t + 1, window_size + 1)
        reward = 0

        if action == 1:  # Buying
            trader.inventory.append(data[t])
            print("AI Trader bought:", stocks_price_format(data[t]))

        elif action == 2 and len(trader.inventory) > 0:  # Selling
            buy_price = trader.inventory.pop(0)

            reward = max(data[t] - buy_price, 0)
            total_profit += data[t] - buy_price
            print("AI Trader sold:", stocks_price_format(data[t]), "Profit: " + stocks_price_format(data[t] - buy_price))

        if t == data_samples - 1:
            done = True
        else:
            done = False

        trader.memory.append((state, action, reward, next_state, done))

        state = next_state

        if done:
            print("########################")
            print("TOTAL PROFIT: {}".format(total_profit))
            print("########################")

    if total_profit > best_profit:
        best_profit = total_profit
        trader.model.save("ai_trader_best.h5")

Episode: 1/10


  0%|          | 0/10694 [00:00<?, ?it/s]

1/1 [==============================] - 0s 18ms/step
AI Trader bought: $ 0.132254
1/1 [==============================] - 0s 20ms/step


  0%|          | 8/10694 [00:00<02:40, 66.42it/s]

AI Trader sold: $ 0.137835 Profit: $ 0.005581
AI Trader bought: $ 0.154018
1/1 [==============================] - 0s 17ms/step
AI Trader sold: $ 0.143973 Profit: - $ 0.010045
AI Trader bought: $ 0.137835
1/1 [==============================] - 0s 17ms/step


...

AI Trader bought: $ 165.229996
AI Trader bought: $ 167.630005
AI Trader bought: $ 166.649994
AI Trader sold: $ 165.020004 Profit: $ 20.800003
AI Trader bought: $ 165.330002
1/1 [==============================] - 0s 25ms/step
AI Trader sold: $ 163.759995 Profit: $ 15.449997
1/1 [==============================] - 0s 24ms/step


100%|█████████▉| 10689/10694 [01:56<00:00, 67.71it/s]

AI Trader bought: $ 168.539993
AI Trader bought: $ 167.449997
AI Trader sold: $ 165.789993 Profit: $ 22.879990
AI Trader bought: $ 173.570007
AI Trader sold: $ 173.500000 Profit: $ 32.559998
1/1 [==============================] - 0s 24ms/step
AI Trader bought: $ 171.770004
AI Trader bought: $ 173.559998
1/1 [==============================] - 0s 24ms/step


100%|██████████| 10694/10694 [01:56<00:00, 91.69it/s]

AI Trader bought: $ 173.750000
########################
TOTAL PROFIT: 1194.9623854197562
########################


### Result:<br>

This Agent give the profit of `$1194.9623854197562` after AI Trader `bought: $ 173.750000` give the best result by buying, selling and staying according to the condition.<br>
This agent trained on GPU tensorflow and save the model name `ai_trader_best.h5` 